In [16]:
# Program za plate solve in astrometrični fits slik.
# Avtor: Bojan Dintinjana, junij 2025
# License: GNU General Public License v3.0
# Uporablja: astrometry.net

import os
import sys
import subprocess
import time
import glob
import re



In [ ]:
# Funkcija za obdelavo ene več datotek 
# lahko teče paralelno v več instancah, vsaaka s svojo listo slik 
def run1(files, vebose=False):

    for file in files:
        solved_file = file.replace('.fits','_wcs.fit')

        # pripravim za morebitni sip polinom
        if sip_order == 0:
            twek_cmd = '--no-tweak'
        else:
            twek_cmd = f'--tweak-order {sip_order}'

        cmd = f"solve-field --cpulimit 10 --no-plots --downsample 3 --objs 300 \
        --resort --overwrite --scale-units arcsecperpix \
        --scale-low {scale_low} --scale-high {scale_high}  \
        --new-fits {solved_file} \
        --index-xyls none --corr none --rdls none --match none --solved none --fits-image \
        --temp-axy {twek_cmd} " + file

        proc = subprocess.Popen(cmd, shell=True, universal_newlines=True, 
                            stdout=subprocess.PIPE, stderr=subprocess.PIPE)

        pixel_scale = ' --  '
        while True:
            nextline = proc.stdout.readline()
            if nextline == '' and proc.poll() is not None:
                break
            # prebere iz izpisa vekikost piksla
            p=re.search(r"RA,Dec .+ pixel scale (?P<s>(\d.\d+)) arcsec/pix.",nextline)
            if p:
                pixel_scale = p.group('s')
            if vebose:
                sys.stdout.write(str(nextline))
            sys.stdout.flush()

        # počakam, da se proces konča
        while proc.poll() == None:
            time.sleep(0.5)

        # izbri začasne datoteke
        os.unlink(file.replace('.fits','.wcs'))

        print(solved_file,pixel_scale,'arcsec/pix' )
    return


In [12]:
path_img = 'M2025-06-12/obdelano/'

files = glob.glob(path_img + 'M13_?_0021.fits')

# približna velikost piksla
# za teleskop Zarja je to ~0.56
# za teleskop Skywatcher je to ~0.93 arcsec/pix
scale_low  = 0.90 
scale_high = 0.94
# nastavim stopnjo sip polinoma 0=brez sip polinom
sip_order=3

# datoteke v obdelavi:
files


['M2025-06-12/obdelano/M13_B_0021.fits',
 'M2025-06-12/obdelano/M13_G_0021.fits']

In [15]:
from multiprocessing import Pool

# nastavim število procesorjev, ki jih bom uporabil
num_processors = 5
# razdelim datoteke v skupine, da jih lahko procesiram hkrati
files_list = [files[0::num_processors]]  
# prva skupina vsebuje vse datoteke, ki so na indeksu 0, 5, 10, 15, ...
# ostale skupine vsebujejo datoteke, ki so na indeksu 1, 2, 3, 4, ..., 6, 7, 8, 9, ...
for i in range(1,num_processors):
	files_list.append(files[i::num_processors])	

# odstranim prazne skupine
files_list = list(filter(None,files_list))

for f in files_list:
	print(len(f),f)	



p = Pool(processes = num_processors)

print('Start multiproces plate-solve ')
_ = p.map(run1, [f for f in files_list])



1 ['M2025-06-12/obdelano/M13_B_0021.fits']
1 ['M2025-06-12/obdelano/M13_G_0021.fits']
Start multiproces plate-solve 
M2025-06-12/obdelano/M13_G_0021_wcs.fit 0.930894 arcsec/pix
M2025-06-12/obdelano/M13_B_0021_wcs.fit 0.931207 arcsec/pix


In [ ]:
"""
Navodilo za pprogram solve-field:
Usage: solve-field [options] <input files>
Options:
 -h / --help: print this help message
  --version: print version string and exit
  -v / --verbose: be more chatty -- repeat for even more verboseness
  -D / --dir <directory>: place all output files in the specified directory
  -o / --out <base-filename>: name the output files with this base name
  -b / --backend-config <filename>: use this config file for the
          "astrometry-engine" program
  --config <filename>: use this config file for the "astrometry-engine" program
  --index-dir <dirname>: search for index files in the given directory, for
          "astrometry-engine"
  --index-file <filename>: add this index file to the "astrometry-engine"
          program; you can quote this and include wildcards.
  --batch: run astrometry-engine once, rather than once per input file
  -f / --files-on-stdin: read filenames to solve on stdin, one per line
  -p / --no-plots: don't create any plots of the results
  --plot-scale <scale>: scale the plots by this factor (eg, 0.25)
  --plot-bg <filename (JPEG)>: set the background image to use for plots
  -G / --use-wget: use wget instead of curl
  -O / --overwrite: overwrite output files if they already exist
  -K / --continue: don't overwrite output files if they already exist; continue
          a previous run
  -J / --skip-solved: skip input files for which the 'solved' output file
          already exists; NOTE: this assumes single-field input files
  --fits-image: assume the input files are FITS images
  -N / --new-fits <filename>: output filename of the new FITS file containing
          the WCS header; "none" to not create this file
  -Z / --kmz <filename>: create KMZ file for Google Sky.  (requires wcs2kml)
  -i / --scamp <filename>: create image object catalog for SCAMP
  -n / --scamp-config <filename>: create SCAMP config file snippet
  -U / --index-xyls <filename>: output filename for xylist containing the image
          coordinate of stars from the index
  --just-augment: just write the augmented xylist files; don't run
          astrometry-engine.
  --axy <filename>: output filename for augment xy list (axy)
  --temp-axy: write 'augmented xy list' (axy) file to a temp file
  --timestamp: add timestamps to log messages
  -7 / --no-delete-temp: don't delete temp files (for debugging)

  -L / --scale-low <scale>: lower bound of image scale estimate
  -H / --scale-high <scale>: upper bound of image scale estimate
  -u / --scale-units <units>: in what units are the lower and upper bounds?
     choices:  "degwidth", "degw", "dw"   : width of the image, in degrees (default)
               "arcminwidth", "amw", "aw" : width of the image, in arcminutes
               "arcsecperpix", "app": arcseconds per pixel
               "focalmm": 35-mm (width-based) equivalent focal length
  -8 / --parity <pos/neg>: only check for matches with positive/negative parity
          (default: try both)
  -c / --code-tolerance <distance>: matching distance for quads (default: 0.01)
  -E / --pixel-error <pixels>: for verification, size of pixel positional error
          (default: 1)
  -q / --quad-size-min <fraction>: minimum size of quads to try, as a fraction
          of the smaller image dimension, default: 0.1
  -Q / --quad-size-max <fraction>: maximum size of quads to try, as a fraction
          of the image hypotenuse, default 1.0
  --odds-to-tune-up <odds>: odds ratio at which to try tuning up a match that
          isn't good enough to solve (default: 1e6)
  --odds-to-solve <odds>: odds ratio at which to consider a field solved
          (default: 1e9)
  --odds-to-reject <odds>: odds ratio at which to reject a hypothesis (default:
          1e-100)
  --odds-to-stop-looking <odds>: odds ratio at which to stop adding stars when
          evaluating a hypothesis (default: LARGE_VAL)
  --use-source-extractor: use SourceExtractor rather than built-in image2xy to
          find sources
  --source-extractor-config <filename>: use the given SourceExtractor config
          file.  Note that CATALOG_NAME and CATALOG_TYPE values will be
          over-ridden by command-line values.  This option implies
          --use-source-extractor.
  --source-extractor-path <filename>: use the given path to the SourceExtractor
          executable.  Default: just 'source-extractor', assumed to be in your
          PATH.  Note that you can give command-line args here too (but put them
          in quotes), eg: --source-extractor-path 'source-extractor -DETECT_TYPE
          CCD'.  This option implies --use-source-extractor.
  -3 / --ra <degrees or hh:mm:ss>: only search in indexes within 'radius' of the
          field center given by 'ra' and 'dec'
  -4 / --dec <degrees or [+-]dd:mm:ss>: only search in indexes within 'radius'
          of the field center given by 'ra' and 'dec'
  -5 / --radius <degrees>: only search in indexes within 'radius' of the field
          center given by ('ra', 'dec')
  -d / --depth <number or range>: number of field objects to look at, or range
          of numbers; 1 is the brightest star, so "-d 10" or "-d 1-10" mean look
          at the top ten brightest stars only.
  --objs <int>: cut the source list to have this many items (after sorting, if
          applicable).
  -l / --cpulimit <seconds>: give up solving after the specified number of
          seconds of CPU time
  -r / --resort: sort the star brightnesses by background-subtracted flux; the
          default is to sort using acompromise between background-subtracted and
          non-background-subtracted flux
  -6 / --extension <int>: FITS extension to read image from.
  --invert: invert the image (for black-on-white images)
  -z / --downsample <int>: downsample the image by factor <int> before running
          source extraction
  --no-background-subtraction: don't try to estimate a smoothly-varying sky
          background during source extraction.
  --sigma <float>: set the noise level in the image
  --nsigma <float>: number of sigma for a source detection; default 8 for FITS
          images, 4 for JPEG, etc
  -9 / --no-remove-lines: don't remove horizontal and vertical overdensities of
          sources.
  --uniformize <int>: select sources uniformly using roughly this many boxes
          (0=disable; default 10)
  --no-verify-uniformize: don't uniformize the field stars during verification
  --no-verify-dedup: don't deduplicate the field stars during verification
  -C / --cancel <filename>: filename whose creation signals the process to stop
  -S / --solved <filename>: output file to mark that the solver succeeded
  -I / --solved-in <filename>: input filename for solved file
  -M / --match <filename>: output filename for match file
  -R / --rdls <filename>: output filename for RDLS file
  --sort-rdls <column>: sort the RDLS file by this column; default is ascending;
          use "-column" to sort "column" in descending order instead.
  --tag <column>: grab tag-along column from index into RDLS file
  --tag-all: grab all tag-along columns from index into RDLS file
  -j / --scamp-ref <filename>: output filename for SCAMP reference catalog
  -B / --corr <filename>: output filename for correspondences
  -W / --wcs <filename>: output filename for WCS file
  -P / --pnm <filename>: save the PNM file as <filename>
  -k / --keep-xylist <filename>: save the (unaugmented) xylist to <filename>
  -A / --dont-augment: quit after writing the unaugmented xylist
  -V / --verify <filename>: try to verify an existing WCS file
  --verify-ext <extension>: HDU from which to read WCS to verify; set this
          BEFORE --verify
  -y / --no-verify: ignore existing WCS headers in FITS input images
  -g / --guess-scale: try to guess the image scale from the FITS headers
  --crpix-center: set the WCS reference point to the image center
  --crpix-x <pix>: set the WCS reference point to the given position
  --crpix-y <pix>: set the WCS reference point to the given position
  -T / --no-tweak: don't fine-tune WCS by computing a SIP polynomial
  -t / --tweak-order <int>: polynomial order of SIP WCS corrections
  --predistort <filename>: apply the inverse distortion in this SIP WCS header
          before solving
  --xscale <factor>: for rectangular pixels: factor to apply to measured X
          positions to make pixels square
  -m / --temp-dir <dir>: where to put temp files, default /tmp
The following options are valid for xylist inputs only:
  -F / --fields <number or range>: the FITS extension(s) to solve, inclusive
  -w / --width <pixels>: specify the field width
  -e / --height <pixels>: specify the field height
  -X / --x-column <column-name>: the FITS column containing the X coordinate of
          the sources
  -Y / --y-column <column-name>: the FITS column containing the Y coordinate of
          the sources
  -s / --sort-column <column-name>: the FITS column that should be used to sort
          the sources
  -a / --sort-ascending: sort in ascending order (smallest first); default is
          descending order

Note that most output files can be disabled by setting the filename to "none".
 (If you have a sick sense of humour and you really want to name your output
  file "none", you can use "./none" instead.)
"""


In [ ]:

num_processors = 5
# razdelim datoteke v skupine, da jih lahko procesiram hkrati
files_list = [files[0::5], files[1::5], files[2::5], files[3::5], files[4::5]]
files_list = list(filter(None,files_list))

for f in files_list:
	print(len(f),f)	


files_list1 = [files[0::num_processors]]  
# prva skupina vsebuje vse datoteke, ki so na indeksu 0, 5, 10, 15, ...
# ostale skupine vsebujejo datoteke, ki so na indeksu 1, 2, 3, 4, ..., 6, 7, 8, 9, ...
for i in range(1,num_processors):
	files_list1.append(files[i::num_processors])	
files_list1 = list(filter(None,files_list1))

for f in files_list1:
	print(len(f),f)	



